In [1]:
import glob
import os
import h5py
import astropy.cosmology
import numpy as np
from pycbc import cosmology
from pycbc import waveform
from pycbc import conversions as con    

In [2]:
from pycbc import catalog
c = catalog.Catalog(source='gwtc-3')

In [3]:
astropy.cosmology.FlatLambdaCDM.comoving_volume

<function astropy.cosmology.core.FLRW.comoving_volume(self, z)>

In [4]:
cosmology.cosmological_quantity_from_redshift(cosmology.redshift(7000),'comoving_volume')

173077981687.57034

In [5]:
cosmology.redshift()

TypeError: redshift() missing 1 required positional argument: 'distance'

In [6]:
def LVKpos(name):
    h5file = glob.glob('/work/yifan.wang/4ogc/LVK/GWTC-3/*'+str(name)+'*_cosmo.h5')
    f = h5py.File(h5file[0],'r')
    # parameters
    mc = f['C01:Mixed']['posterior_samples']['chirp_mass_source'][:]
    q = 1/f['C01:Mixed']['posterior_samples']['mass_ratio'][:]
    z = f['C01:Mixed']['posterior_samples']['redshift'][:]
    # prior range
    mchigh = np.ceil(np.quantile(mc,0.99))
    mclow = np.floor(np.quantile(mc,0.01))
    qhigh = np.ceil(np.quantile(q,0.99))
    zhigh = np.max(z)
    comvhigh = cosmology.cosmological_quantity_from_redshift(zhigh,'comoving_volume')
    if comvhigh < 1e10:
        comvhigh += 3e9
    else:
        comvhigh +=3e10 #add some offset
        
    #starting time
    m1 = con.mass1_from_mchirp_q(mclow,1)
    m2 = con.mass2_from_mchirp_q(mclow,1)
    t = waveform.get_waveform_filter_length_in_time(approximant='IMRPhenomXPHM', mass1=m1,mass2=m2,f_lower=20)
    start_time = -np.ceil(t)
    f.close()
    return mclow,mchigh,qhigh,int(comvhigh),int(start_time)

In [7]:
try:
    os.remove('events.ini')
except FileNotFoundError:
    pass

allfile = glob.glob('config_file/*.ini')
print(allfile)
def custom(name):
    return name.split('-')[1]

allfile.sort(key=custom)
print(allfile)

with open('events.ini', 'a') as f:
    for directory in allfile:
        fname = os.path.basename(directory)
        fname = fname[5:20]
        print(fname)
        mclow,mchigh,qhigh,comvhigh,start_time = LVKpos(fname)
        print(LVKpos(fname))
        calfile = glob.glob('calibration_file/*'+str(fname)+'*.ini')
        f.write('[event-'+str(fname)+']\n')
        f.write('label = '+str(fname)+'\n')
        f.write('config-files = '+str(directory) +
                '\n \t\t' + str(calfile[0]) + '\n\t\tinference.ini\n')
        f.write('config-overrides = \n')
        #override
        f.write('\t\t\tprior-srcmchirp:min-srcmchirp:%d\n' % mclow)
        f.write('\t\t\tprior-srcmchirp:max-srcmchirp:%d\n' % mchigh)
        f.write('\t\t\tprior-q:max-q:%d\n' % qhigh)
        f.write('\t\t\tprior-comoving_volume:max-comoving_volume:%.d\n' % comvhigh)
        f.write('\t\t\tdata:analysis-start-time:%d\n' % start_time)
        
        #PSD time translation
        if fname=='GW191109_010717':
            f.write('\t\t\tdata:psd-start-time:"H1:-100 L1:-256"\n')
            f.write('\t\t\tdata:psd-end-time:"H1:412 L1:256"\n')
        if fname == 'GW191113_071753':
            f.write('\t\t\tdata:psd-start-time:"H1:-100 L1:-256 V1:-256"\n')
            f.write('\t\t\tdata:psd-end-time:"H1:412 L1:256 V1:256"\n')
        if fname == 'GW191105_143521':
            f.write('\t\t\tdata:psd-start-time:"H1:-256 L1:-256 V1:-412"\n')
            f.write('\t\t\tdata:psd-end-time:"H1:256 L1:256 V1:100"\n')
            
        f.write('\n')
f.close()

['config_file/data-GW191127_050227.ini', 'config_file/data-GW191105_143521.ini', 'config_file/data-GW191215_223052.ini', 'config_file/data-GW191204_110529.ini', 'config_file/data-GW191216_213338.ini', 'config_file/data-GW191109_010717.ini', 'config_file/data-GW191204_171526.ini', 'config_file/data-GW191113_071753.ini', 'config_file/data-GW191126_115259.ini', 'config_file/data-GW191103_012549.ini', 'config_file/data-GW191219_163120.ini', 'config_file/data-GW191129_134029.ini']
['config_file/data-GW191103_012549.ini', 'config_file/data-GW191105_143521.ini', 'config_file/data-GW191109_010717.ini', 'config_file/data-GW191113_071753.ini', 'config_file/data-GW191126_115259.ini', 'config_file/data-GW191127_050227.ini', 'config_file/data-GW191129_134029.ini', 'config_file/data-GW191204_110529.ini', 'config_file/data-GW191204_171526.ini', 'config_file/data-GW191215_223052.ini', 'config_file/data-GW191216_213338.ini', 'config_file/data-GW191219_163120.ini']
GW191103_012549
(7.0, 10.0, 5.0, 52136